# Environment Setting

In [37]:
!pip install 'Fiona==1.8.18'
!pip install 'Shapely==1.7.1'
!pip install 'pyproj==3.0.0.post1'
!pip install geojson
!pip install folium


In [38]:
import boto3
from branca.colormap import linear
import fiona
import folium
import pandas as pd
import numpy as np
from pyproj import Proj, transform
import os


import warnings
warnings.filterwarnings('ignore')

In [39]:
from shapely.geometry import shape

In [40]:
%load_ext autoreload
%autoreload 2

import sys

sys.path.append("..")

from src.utils import S3Utils, athena_to_pandas

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [41]:
codreg_dict = {
    'Piemonte': 1,
    "Valle d'Aosta": 2,
    "Lombardia": 3,
    "Trentino Alto Adige": 4,
    "Veneto": 5,
    "Friuli Venezia Giulia": 6,
    "Liguria": 7,
    "Emilia-Romagna": 8,
    "Toscana": 9,
    "Umbria": 10,
    "Marche": 11,
    "Lazio": 12,
    "Abruzzo": 13,
    "Molise": 14,
    "Campania": 15,
    "Puglia": 16,
    "Basilicata": 17,
    "Calabria": 18,
    "Sicilia": 19,
    "Sardegna": 20}

In [45]:
def wkt_to_geojson(wkt):
    
    g1 = shapely.wkt.loads(wkt)
    g2 = geojson.Feature(geometry=g1, properties={})
    return g2.geometry

In [42]:
workgroup = 'primary'
output_bucket = 'athena-staging-eu-south'
staging_key = 'athena-staging'
athena_region = 'eu-south-1'

### Plot all areas for a single Comune

In [99]:
%%time
region = 'Lombardia'
comune = 'Milano'
reg_cod = codreg_dict[region]

params = {'comune': comune,
          'reg_cod': reg_cod}


sql_query = """
    select a.*,
    ST_Centroid(b.geometry_wkt_ll) as centroid,
    b.geometry_wkt_ll as geometry_ll
    
    from gimi.census_areas_features_2011 a
    
    left join (select * from gimi.census_areas_2011 where cod_reg = {reg_cod} ) b
    
    on a.sez2011 = b.sez2011
    where a.codreg = {reg_cod} 
    and a.comune = '{comune}'
    
    """.format(**params)

feats = athena_to_pandas(sql_query, workgroup, output_bucket, staging_key, athena_region)

# Convert to GeoJson
feats['geometry_geojson'] = [wkt_to_geojson(x) for x in feats['geometry_ll']]
feats['centroid_geojson'] = [wkt_to_geojson(x) for x in feats['centroid']]

Execution Succeded
CPU times: user 1.76 s, sys: 24.7 ms, total: 1.78 s
Wall time: 8.08 s


In [100]:
len(feats)

6017

In [101]:
# Find Area Centroid
cents = [x['coordinates'] for x in feats['centroid_geojson']]

longs = [x[0] for x in cents]
lats = [x[1] for x in cents]

centroid = (np.mean(lats), np.mean(longs))

In [102]:
color_variable = 'p1'
id_col = 'sez2011'

# Create a color map based on the Variable of interest
color_data = feats[[id_col, color_variable]]
colormap = linear.YlGn_09.scale(
    color_data[color_variable].min(), color_data[color_variable].max()
)

color_dict = color_data.set_index(id_col)[color_variable]



# Find area centroid to inizialize the Map

# Create Feature Collection
feat_coll = []

for cel in feats.itertuples():
    
    geo = cel.geometry_geojson.copy()
    new_geo = {
             'type': 'Feature', 
             'geometry': geo, 
             'id': cel.sez2011,
             'properties': {'Provincia': cel.provincia,
                            'Comune': cel.comune,
                            'Sezione': cel.sez2011,
                            'Value': cel.p1,
                            'Popolazione': cel.p1,
                            'Infanti': cel.p14,
                            'Laureati': cel.p47
                            }
             }
    feat_coll.append(new_geo)

geo_json_data = {'type': 'FeatureCollection',
                 'features': feat_coll}
  
# Plot Data
m = folium.Map(centroid, zoom_start=10)
folium.GeoJson(geo_json_data,
               popup=folium.GeoJsonPopup(fields = ['Provincia', 'Comune', 'Sezione', 'Value', 'Popolazione', 'Infanti', 'Laureati']),
               style_function=lambda feature: {
                  "fillColor": colormap(color_dict[feature["id"]]),
                  "color": "black",
                  "weight": 3,
                  "dashArray": "5, 5",
                  "fillOpacity": 0.4,
              }
               
               ).add_to(m)

m